# <span style="color:purple">Cartopy 2: NYS Mesonet Data</span>

### In this notebook, we'll use Cartopy, Matplotlib, Datetime, and Pandas to visualize data from the <a href="http://www.nysmesonet.org/">New York State Mesonet</a>, headquartered right here at UAlbany.

In [ ]:
import matplotlib.pyplot as plt
import pandas as pd
from cartopy import crs as ccrs
from cartopy import feature as cfeature
from datetime import datetime

### Create a regional map, centered over NYS, and add in some geographic features.
#### <span style="color: red"><b>Be patient</b></span>: this may take a minute or so to plot, depending on the resolution of the Natural Earth shapefile features you are adding! 

<img src = "NaturalEarthScales.png" width=800 height=600 />

<a img="images/NaturalEarthScales.png"></a>

## Create the figure
#### For a quick look, let's just choose the coarsest (110,000,000:1) Natural Earth shapefiles set.

In [ ]:
# Set the domain for defining the plot region.
latN = 45.2
latS = 40.2
lonW = -80.0
lonE = -71.5
cLat = (latN + latS)/2
cLon = (lonW + lonE )/2


proj = ccrs.LambertConformal(central_longitude=cLon, central_latitude=cLat)

res = '110m' # Coarsest and quickest to display; other options are '10m' (slowest) and '50m'.

fig = plt.figure(figsize=(11,8.5),dpi=125)
ax = plt.subplot(1,1,1,projection=proj)
ax.set_extent ([lonW,lonE,latS,latN])
ax.add_feature(cfeature.COASTLINE.with_scale(res))
ax.add_feature (cfeature.STATES.with_scale(res));

### Plot some data on the map. We'll use Pandas to read in the file containing the most recent NYS Mesonet obs.


In [ ]:
df = pd.read_csv('http://www.atmos.albany.edu/products/nysm/nysm_latest.csv')

### View the first and last five lines of this `DataFrame`

In [ ]:
df

Specify a couple of sites using Pandas' `query` function.

In [ ]:
df.query('station == "LAUR"')

In [ ]:
df.query('station == "LKPL"')

Examine the column names.

In [ ]:
df.columns

### Create objects pointing to some columns of interest. In Pandas, we can refer to columns by using a "." in addtion to "[]" in most circumstances, though not if a column name starts with a number, nor if there are spaces in the column name.

In [ ]:
stid = df.station
lat = df.lat
lon = df.lon
tmp2 = df['temp_2m [degC]'] # Use brackets due to the presence of a space in the column name
tmp9 = df['temp_9m [degC]']
time = df.time

We will plot one of the variables on a map later on in this notebook. In case we want to go back later and pick a different variable to plot (e.g. 9 m temperature), let's define a generic object name. 

In [ ]:
param = tmp9 # replace with tmp9, e.g., if you want to plot 9 m temperature

In [ ]:
param

Let's look at the time object.

In [ ]:
time

#### The times are the same for all stations, so let's just pull out one of them, and then create some formatted datetime strings out of it.

In [ ]:
timeString = time[0]
timeString

#### The `timeString` above could make for a perfectly fine part of an informative title for a map, but let's create a string of the form "Month Day, Year, HourMin UTC" (e.g., *Mar 30, 2021, 0120 UTC* )
First, make a `datetime` object from the string, using `strptime` with a format that matches that of the string.

In [ ]:
timeObj = datetime.strptime(timeString,"%Y-%m-%d %H:%M:%S")
timeObj

Next, make a `string` object from the `datetime` object, using `strftime` with a format that matches what we want to use in the map's title.

In [ ]:
titleString = datetime.strftime(timeObj,"%B %d %Y, %H%M UTC")

In [ ]:
titleString

### Create a scatterplot to show the locations of each NYS Mesonet site using Matplotlib's `scatter` method. This method accepts an entire array of lon-lat values.

In [ ]:
ax.set_title ('New York State Mesonet Site Locations')
ax.scatter(lon,lat,s=9,c='r',edgecolor='black',alpha=0.75,transform=ccrs.PlateCarree())
# Plot the figure, now with the sites plotted
fig

### <span style="color: red"> Did you notice the `transform` argument? </span> Since we are plotting on a Lambert Conformal-projected map, which uses a Cartesian x-y coordinate system where each point is equally separated in meters, we need to convert, or *transform*, the lat-lon coordinates into their equivalent coordinates in our chosen projection. We use the `transform` argument, and assign its value to the coordinate system that our lat-lon array is derived from.

### Next, plot the site IDs, using Matplotlib's `text` method. This method only accepts a single value for its x and y coordinates, so we need to loop over all the values in the arrays.

## Python's `enumerate` function:
In a Python `list`, one can use the `enumerate` function to set a numerical value to be used as a counter variable (see, e.g.. https://realpython.com/python-enumerate/), while at the same time assigning the corresponding list element's value to another variable. We can use the same technique on a Pandas `series` object:

In [ ]:
for count, value in enumerate(stid):
    print (count, value)

In the above example, `count` represents the row index number in the Pandas series, while `value` is its corresponding value. E.g., the first element's `count` is 0, while the `value` is **ADDI**. The `for` loop iterates through all (127) elements of the series. 

Now, we can iterate over all 127 sites. For each site, we use Matplotlib's `ax.text` function to plot the site ID at its corresponding longitude and latitude. E.g., the first site (**ADDI**, when `count = 0`)'s longitude is **-77.237260** and its latitude is **42.040360**.		

In [ ]:
for count, value in enumerate(stid):
    ax.text(lon[count],lat[count],value,horizontalalignment='right',transform=ccrs.PlateCarree(),fontsize=7)

In [ ]:
fig

Now, let's attempt to plot the site locations again, but this time we'll **omit** the `transform` argument in `ax.scatter` and `ax.text`. 

In [ ]:
fig = plt.figure(figsize=(11,8.5),dpi=125)
ax = plt.subplot(1,1,1,projection=proj)
ax.set_extent ([lonW,lonE,latS,latN])
ax.add_feature(cfeature.COASTLINE.with_scale(res))
ax.add_feature (cfeature.STATES.with_scale(res))
ax.set_title ('New York State Mesonet Site Locations')
ax.scatter(lon,lat,s=9,c='r',edgecolor='black',alpha=0.75)
for count, site in enumerate(stid):
    ax.text(lon[count],lat[count],site,horizontalalignment='right',fontsize=7)

### What do you think happened here?

<div class="admonition alert alert-warning">
    <p class="admonition-title" style="font-weight:bold">Exercise</p>
    Create a new figure which plots the current 2m temperature at the NYSM sites. Include the current date/time to the title.
</div>

In [ ]:
# %load '/spare11/atm350/common/mar25/cartopy_2.py'
proj = ccrs.LambertConformal(central_longitude=cLon, central_latitude=cLat)
res = '50m' # Use the medium-resolution shapefiles

fig = plt.figure(figsize=(15,10),dpi=125)
ax = plt.subplot(1,1,1,projection=proj)
ax.set_extent ([lonW,lonE,latS,latN])
ax.set_title(f"NYS Mesonet 2 meter temperature (°C), {titleString}")
ax.add_feature(cfeature.COASTLINE.with_scale(res))
ax.add_feature (cfeature.STATES.with_scale(res));

for count, value in enumerate(param):
    ax.text(lon[count],lat[count],value,horizontalalignment='right',transform=ccrs.PlateCarree(),fontsize=7,color='blue')


#### Now, plot a different variable ... 9 meter temperature. We just need to reset `param`'s value so it points to the 9-m temperature series; we can repeat the exact same cell as we used above, except we do need to modify the figure title so it reflects what variable we are using.

In [ ]:
param = tmp9

fig = plt.figure(figsize=(15,10),dpi=125)
ax = plt.subplot(1,1,1,projection=proj)
ax.set_extent ([lonW,lonE,latS,latN])
ax.set_title(f"NYS Mesonet 9 meter temperature (°C), {titleString}")
ax.add_feature(cfeature.COASTLINE.with_scale(res))
ax.add_feature (cfeature.STATES.with_scale(res));

for count, value in enumerate(param):
    ax.text(lon[count],lat[count],value,horizontalalignment='right',transform=ccrs.PlateCarree(),fontsize=7,color='blue')


### We could plot additional variables, and in so doing create a standard surface station plot, but we would find it challenging to align all the variables around the points corresponding to the NYS Mesonet sites. Fortunately, Metpy's `StationPlot` method takes care of this, and we will be using it in upcoming notebooks!

#### Sneak preview: [Latest NYSM Surface Map](http://www.atmos.albany.edu/facstaff/ktyle/nysm/sfcmap.png)